
# Pulsed Breakdown Model

This example demonstrates the RepetitivePulseBreakdownModel which calculates breakdown voltage
with memory effects from repetitive pulsing.


In [ ]:
import matplotlib.pyplot as plt
import numpy as np
import openmdao.api as om

from paroto.models.breakdown_voltage import RepetitivePulseBreakdownModel

# Create OpenMDAO problem
prob = om.Problem()
prob.model.add_subsystem(
    "breakdown",
    RepetitivePulseBreakdownModel(
        model_parameters={
            "A_paschen": 24.4,
            "B_paschen": 6.73,
            "field_enhancement_factor": 1.0,
            "ionization_time": 1e-7,
            "pulse_amplitude_factor": 4.0,
            "decay_constant": 1.0,
        }
    ),
)
prob.setup()

# Set common parameters
prob.set_val("breakdown.gas_properties_pressure", 101325.0)  # 1 atm
prob.set_val("breakdown.preheat_temperature", 300.0)  # K
prob.set_val("breakdown.gap_distance", 0.01)  # 10 mm
prob.set_val("breakdown.pulse_frequency", 50e3)  # 50 kHz
prob.set_val("breakdown.pulse_duration", 1e-6)  # 1 μs

print("=" * 60)
print("Pulsed Breakdown Model - Memory Effects")
print("=" * 60)

# Test for different number of pulses
n_pulses_list = [1, 10, 100]

for n_pulses in n_pulses_list:
    # Residence time determines number of pulses
    t_res = n_pulses / 50e3  # seconds

    prob.set_val("breakdown.residence_time", t_res)
    prob.run_model()

    V_bd = prob.get_val("breakdown.breakdown_voltage")[0]
    print(f"N = {n_pulses:3d} pulses: V_breakdown = {V_bd:.0f} V")

print("=" * 60)
print("Note: Breakdown voltage decreases with more pulses")
print("      (memory effect from repetitive pulsing)")
print("=" * 60)

# Plot breakdown voltage vs number of pulses
print("\nGenerating plot: Breakdown Voltage vs Number of Pulses...")
n_pulses_range = np.logspace(0, 3, 50)  # 1 to 1000 pulses
V_bd_values = []

for n_pulses in n_pulses_range:
    t_res = n_pulses / 50e3  # seconds
    prob.set_val("breakdown.residence_time", t_res)
    prob.run_model()
    V_bd_values.append(prob.get_val("breakdown.breakdown_voltage")[0])

plt.figure(figsize=(8, 5))
plt.semilogx(n_pulses_range, V_bd_values, "b-", linewidth=2)
plt.xlabel("Number of Pulses")
plt.ylabel("Breakdown Voltage (V)")
plt.title("Breakdown Voltage vs Number of Pulses (Memory Effect)")
plt.grid(True, alpha=0.3, which="both")
plt.tight_layout()
plt.show()